In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns


In [5]:
pip install transformers and torch

ERROR: Could not find a version that satisfies the requirement and (from versions: none)
ERROR: No matching distribution found for and


In [3]:
import os
import torch
import gradio as gr
from transformers import AutoTokenizer, AutoModelForCausalLM

# -------- Model loading --------
MODEL_NAME = os.getenv("MODEL_NAME", "gpt2")  # you can set to gpt2-medium via Space secrets/variables

device = "cuda" if torch.cuda.is_available() else "cpu"

tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
# GPT-2 has no pad token by default; set it to EOS to avoid warnings
if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token

model = AutoModelForCausalLM.from_pretrained(MODEL_NAME)
model.to(device)
model.eval()

# -------- Generation helper --------
TONE_PRESETS = {
    "Neutral": "neutral, informative, and clear",
    "Professional": "formal, concise, and authoritative",
    "Friendly": "warm, engaging, and helpful",
    "Persuasive": "confident, compelling, and benefit-focused",
    "Storytelling": "narrative, vivid, and descriptive",
}

LENGTH_TO_TOKENS = {
    "Short (~300-500 words)": 380,
    "Medium (~600-900 words)": 720,
    "Long (~1000-1400 words)": 1080,
}


def build_prompt(title: str, outline: str, tone_label: str) -> str:
    tone = TONE_PRESETS.get(tone_label, TONE_PRESETS["Neutral"])
    outline_block = f"\nOutline:\n{outline.strip()}\n" if outline and outline.strip() else "\n"

    prompt = (
        f"You are a senior content writer. Write a high-quality blog article.\n"
        f"Title: {title.strip()}\n"
        f"Tone: {tone}\n"
        f"Audience: general readers with interest in the topic.\n"
        f"Structure: catchy introduction, well-organized sections with subheadings, bullet points where helpful, and a concluding takeaway.\n"
        f"Use simple language, avoid fluff, and keep paragraphs short.\n"
        f"Add a short, compelling meta description at the end.\n"
        f"{outline_block}\n"
        f"Begin the article below:\n"
    )
    return prompt


def generate_blog(title, outline, tone, length_choice, temperature, top_p, top_k, repetition_penalty, seed):
    if not title or not title.strip():
        return "Please provide a blog title/topic."

    if seed is not None and seed != "":
        try:
            seed_int = int(seed)
            torch.manual_seed(seed_int)
            if torch.cuda.is_available():
                torch.cuda.manual_seed_all(seed_int)
        except ValueError:
            pass

    prompt = build_prompt(title, outline, tone)

    inputs = tokenizer(prompt, return_tensors="pt")
    input_len = inputs["input_ids"].shape[-1]
    inputs = {k: v.to(device) for k, v in inputs.items()}

    max_new_tokens = LENGTH_TO_TOKENS.get(length_choice, 720)

    with torch.inference_mode():
        output_ids = model.generate(
            **inputs,
            max_new_tokens=max_new_tokens,
            do_sample=True,
            temperature=float(temperature),
            top_p=float(top_p),
            top_k=int(top_k),
            repetition_penalty=float(repetition_penalty),
            pad_token_id=tokenizer.eos_token_id,
            eos_token_id=tokenizer.eos_token_id,
        )

    generated = tokenizer.decode(output_ids[0][input_len:], skip_special_tokens=True)

    # Light post-process: ensure it starts clean and trim over-long endings
    text = generated.strip()

    # Safety note
    disclaimer = (
        "\n\n\n—\nNote: This draft is AI-generated using a pretrained GPT‑2 model. "
        "Facts may be inaccurate. Please review and edit before publishing."
    )
    return text + disclaimer


# -------- Gradio UI --------
with gr.Blocks(title="Blog Generator • GPT‑2") as demo:
    gr.Markdown(
        "# ✍️ Blog Generator (GPT‑2)\n"
        "Generate blog drafts with a pretrained GPT‑2 model. "
        "For best results, write a clear title and (optional) outline."
    )

    with gr.Row():
        title = gr.Textbox(label="Blog Title / Topic", placeholder="e.g., How to Start a Budget in 2025", lines=1)

    outline = gr.Textbox(
        label="Optional Outline or Notes",
        placeholder="Bullet points, key sections, facts to include…",
        lines=8,
    )

    with gr.Row():
        tone = gr.Dropdown(
            choices=list(TONE_PRESETS.keys()),
            value="Neutral",
            label="Tone",
        )
        length_choice = gr.Radio(
            choices=list(LENGTH_TO_TOKENS.keys()),
            value="Medium (~600-900 words)",
            label="Length",
        )

    with gr.Accordion("Advanced Settings", open=False):
        with gr.Row():
            temperature = gr.Slider(0.1, 1.5, value=0.9, step=0.05, label="Temperature")
            top_p = gr.Slider(0.1, 1.0, value=0.95, step=0.01, label="Top-p")
            top_k = gr.Slider(0, 200, value=50, step=1, label="Top-k")
        with gr.Row():
            repetition_penalty = gr.Slider(1.0, 2.0, value=1.12, step=0.01, label="Repetition Penalty")
            seed = gr.Textbox(label="Seed (optional, for reproducibility)", placeholder="e.g., 42")

    generate_btn = gr.Button("Generate Article", variant="primary")
    output = gr.Textbox(label="Draft Article", lines=28)

    generate_btn.click(
        fn=generate_blog,
        inputs=[title, outline, tone, length_choice, temperature, top_p, top_k, repetition_penalty, seed],
        outputs=output,
        api_name="generate",
    )

    gr.Markdown(
        "**Tips**: If the text loops or gets off-topic, lower temperature or top‑p, increase repetition penalty, or add a more detailed outline.\n"
        "**Model**: Using `" + MODEL_NAME + "`. You can set a different model name via the `MODEL_NAME` environment variable in your Space Settings."
    )

if __name__ == "__main__":
    demo.queue().launch()

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

It looks like you are running Gradio on a hosted Jupyter notebook, which requires `share=True`. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://7c98a0f09e520deeb3.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
